In [1]:
import os
os.environ["CUDA_DEVICE_ORDER"]="PCI_BUS_ID"
os.environ["CUDA_VISIBLE_DEVICES"]="3"
import torch
torch.cuda.set_device(0)
torch.cuda.current_device()

0

In [2]:
import torch
from transformers import T5Tokenizer, T5ForConditionalGeneration

from accelerate import Accelerator

class Summarizer:
    def __init__(self, device="cpu"):
        model_name = "sarahai/ruT5-base-summarizer"
        self.device = device
        self.tokenizer  = T5Tokenizer.from_pretrained(model_name, device_map=device)
        self.model = T5ForConditionalGeneration.from_pretrained(model_name, device_map=device)

    def summarize(self, text, max_length=100, min_length=50, num_beams=5):
        input_ids = self.tokenizer(text, return_tensors="pt").input_ids.to(self.device)
        # input_ids = torch.nn.utils.rnn.pad_sequence(input_ids.squeeze().chunk(chunk_num, 0), batch_first=True, padding_value=-100)
        outputs = self.model.generate(input_ids, max_length=max_length,
                                      min_length=min_length,
                                      length_penalty=2.0,
                                      num_beams=num_beams, early_stopping=True)

        return self.tokenizer.decode(outputs[0], skip_special_tokens=True)

    def generate(self, indexes, max_length=100, min_length=50, num_beams=5):
        return self.model.generate(indexes.unsqueeze(0), max_length=max_length,
                                      min_length=min_length,
                                      length_penalty=2.0,
                                      num_beams=num_beams, early_stopping=True).squeeze()

In [3]:
# summarizer = Summarizer("cuda:3")

In [51]:
from bs4 import BeautifulSoup
from pydantic import BaseModel
import requests
from typing import Optional

class Pager(BaseModel):
    title: str
    text: str
    original_tags: list[str]

def is_valid_page(url):
    return True

def get_pager(url)->Optional[Pager]:
    try:
        req = requests.get(url)
        soup = BeautifulSoup(req.text, 'lxml')
        query = soup.find("div", class_="article-formatted-body")
        title = soup.title.string
        tags = []
        for tag in soup.find_all("meta"):
            if tag.get("name", None) == "keywords":
                tags = [x for x in re.split(',| ', tag["content"]) if len(x) > 0]
        return Pager(title=title, text=query.get_text(), original_tags=tags)
    except:
        return None

In [52]:
import re

habr_prefix = "https://habr.com/ru/articles/"
article_prefix = "https://habr.com/ru/"

articles_urls = []


for page_suffix in [""] + [f"page{i}/" for i in range(50)]:
    page_url = habr_prefix + page_suffix
    src = requests.get(page_url).text
    for article_suffix in set(re.findall('articles/\d+/', src)):
        articles_urls.append(article_prefix + article_suffix)

articles_urls

['https://habr.com/ru/articles/897282/',
 'https://habr.com/ru/articles/897472/',
 'https://habr.com/ru/articles/891132/',
 'https://habr.com/ru/articles/897224/',
 'https://habr.com/ru/articles/897636/',
 'https://habr.com/ru/articles/897496/',
 'https://habr.com/ru/articles/897630/',
 'https://habr.com/ru/articles/897518/',
 'https://habr.com/ru/articles/897640/',
 'https://habr.com/ru/articles/897574/',
 'https://habr.com/ru/articles/897632/',
 'https://habr.com/ru/articles/891488/',
 'https://habr.com/ru/articles/896972/',
 'https://habr.com/ru/articles/897624/',
 'https://habr.com/ru/articles/897534/',
 'https://habr.com/ru/articles/897620/',
 'https://habr.com/ru/articles/897654/',
 'https://habr.com/ru/articles/897648/',
 'https://habr.com/ru/articles/897642/',
 'https://habr.com/ru/articles/897634/',
 'https://habr.com/ru/articles/897282/',
 'https://habr.com/ru/articles/897472/',
 'https://habr.com/ru/articles/891132/',
 'https://habr.com/ru/articles/897224/',
 'https://habr.c

In [53]:
len(articles_urls)

1000

In [54]:
import time
from tqdm import tqdm

pagers = []

for url in tqdm(articles_urls):
    pagers.append(get_pager(url))
    

100%|██████████████████████████| 1000/1000 [09:35<00:00,  1.74it/s]


In [55]:
pagers = [x for x in pagers if x is not None]
len(pagers)

1000

In [56]:
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
stop_words = set(stopwords.words('russian'))

stop_words

for pager in pagers:
    pager.original_tags = list(set([x for x in pager.original_tags if x not in stop_words]))

In [57]:
# summarizer = Summarizer("cuda")

for pager in pagers:
    pager.text = pager.text[:3000]

In [58]:
import pandas as pd

df = pd.DataFrame([pager.dict() for pager in pagers])
df

/tmp/ipykernel_57433/3926614870.py:3: PydanticDeprecatedSince20: The `dict` method is deprecated; use `model_dump` instead. Deprecated in Pydantic V2.0 to be removed in V3.0. See Pydantic V2 Migration Guide at https://errors.pydantic.dev/2.10/migration/
  df = pd.DataFrame([pager.dict() for pager in pagers])


title  \
0    Раскраска листинга процедуры T-SQL значениями ...   
1    Искусственный интеллект и алгоритмы в энергети...   
2    «Эти фильмы были ужасны» — короткий рассказ о ...   
3    Что будет, если не использовать TCP или UDP? /...   
4      Почему тренд на аэрошоссеры возвращаются / Хабр   
..                                                 ...   
995  Service Mesh в дикой природе или как не стать ...   
996    Apple Pro Weekly News (17.03 – 23.03.25) / Хабр   
997  Как не завязнуть в болоте рутины и оставаться ...   
998                            Релиз Linux 6.14 / Хабр   
999     Чтобы побеждать, достаточно одной книги / Хабр   

                                                  text  \
0    Сразу покажу, о чем идет речь, чтобы вы решили...   
1    Энергетические системы — одни из самых сложных...   
2    Концепт-арт к «Ксеногенезису» (1978) — к так и...   
3    Коммутаторы, маршрутизаторы, брандмауэры — все...   
4    Почему аэрошоссеры возвращаются в 2025 годуНес...   
..                                                 ...   
995  ВведениеУгрозы безопасности в Service Mesh1. О...   
996  Что сломали в последнем обновлении iOS, от чег...   
997  С того момента, как я начал работать IT менедж...   
998  24 марта 2025 года Линус Торвальдс представил ...   
999  \nЕсть два правдивых утверждения.\n\nПервое пр...   

                                         original_tags  
0           [sql, tsql, markup, profiler, performance]  
1    [алгоритмы, ии, ит, интеллект, лэп, энергетика...  
2    [кино, рисование, фильмы, фантастика, эффекты,...  
3    [эксперимент, данных, tcp, передача, протоколы...  
4    [скорость, вес, шоссейный, аэротруба, велосипе...  
..                                                 ...  
995  [безопасность, приложений, микросервисы, микро...  
996  [Apple, Siri, iMazing, iPhone, App, iPad, iOS,...  
997  [командой, проектов, руководство, проектами, л...  
998                           [6.14, Linux, торвальдс]  
999  [ruvds_перевод, техническая, программиста, лит...  

[1000 rows x 3 columns]

In [62]:
df.to_csv("pagers.csv")

In [4]:
model_name = "sarahai/ruT5-base-summarizer"
tokenizer = T5Tokenizer.from_pretrained(model_name, device_map="cpu")

In [5]:
import pandas as pd
df = pd.read_csv("pagers.csv")

In [6]:
from torch.nn.utils.rnn import pad_sequence

class PagerDataset:
    def __init__(self, device="cpu", pagers=df):
        model_name = "sarahai/ruT5-base-summarizer"
        self.device = device
        self.tokenizer  = T5Tokenizer.from_pretrained(model_name, device_map=device)
        self.texts = [self.tokenizer(pager, return_tensors="pt").input_ids[0] for pager in pagers['text']]
        self.tags = [self.tokenizer(' '.join(eval(pager)), return_tensors="pt").input_ids[0] for pager in pagers['original_tags']]

    def __len__(self):
        return len(self.tags)

    def __getitem__(self, index):
        return self.texts[index], self.tags[index]

class PagerCollator:
    @staticmethod
    def collate_tokens(tokens_batch, padding_value):
        return pad_sequence(tokens_batch, batch_first=True, padding_value=padding_value).to(torch.long)

    def __call__(self, batch):
        values = [item[0] for item in batch]
        labels = [item[1] for item in batch]
        input_values = PagerCollator.collate_tokens(values, 0)
        mask = (input_values == PagerCollator.collate_tokens(values, 1)).to(torch.long)
        labels = PagerCollator.collate_tokens(labels, -100)

        return {
            'input_ids': input_values, 
            'labels': labels,
            'attention_mask': mask
        }


In [7]:
threshold = int(len(df) * 0.9)

train_set = df.sample(threshold)


train = PagerDataset(pagers=train_set)
test = PagerDataset(pagers=df.drop(index = train_set.index))

In [8]:
train_set['text']

45     Привет! Меня зовут Ирина, уже более пяти лет я...
562    Всем привет! На связи Николай Едомский, руково...
448    В одном из больших кластеров S3 в Точке хранит...
727    Моя история проста как три копейки. В конце 20...
282    Недавно в Общественной палате России состоялся...
                             ...                        
802    Arcana OPS — это современный подход к управлен...
2      Концепт-арт к «Ксеногенезису» (1978) — к так и...
583    По прогнозу Gartner, запросы на естественном я...
100    Все современные средства разработки — практиче...
470    \nЯ слушаю аудиокниги с 2014 года. За это врем...
Name: text, Length: 900, dtype: object

In [9]:
from transformers import T5Tokenizer, T5ForConditionalGeneration

model_name = "sarahai/ruT5-base-summarizer"
model = T5ForConditionalGeneration.from_pretrained(model_name, device_map="cuda")

model.resize_token_embeddings(len(tokenizer))

Embedding(32100, 768)

In [10]:
from transformers import TrainingArguments

training_args = TrainingArguments(
    output_dir="test",
    per_device_train_batch_size=8,
    gradient_accumulation_steps=1,
    evaluation_strategy="steps",
    max_steps=4000,
    fp16=False,
    save_steps=2000,
    eval_steps=32,
    logging_steps=30,
    learning_rate=1e-3,
    weight_decay=0.007,
    warmup_steps=250,
    gradient_checkpointing=True,
    report_to=[],
)

/home/semikrasal/.local/lib/python3.10/site-packages/transformers/training_args.py:1594: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


In [11]:
from transformers import Trainer

trainer = Trainer(
    model=model,
    data_collator=PagerCollator(),
    args=training_args,
    train_dataset=train,
    eval_dataset=test,
)

In [12]:
trainer.train()

`use_cache=True` is incompatible with gradient checkpointing. Setting `use_cache=False`...


Passing a tuple of `past_key_values` is deprecated and will be removed in Transformers v4.48.0. You should pass an instance of `EncoderDecoderCache` instead, e.g. `past_key_values=EncoderDecoderCache.from_legacy_cache(past_key_values)`.


TrainOutput(global_step=4000, training_loss=0.8493731454242952, metrics={'train_runtime': 5394.6282, 'train_samples_per_second': 5.932, 'train_steps_per_second': 0.741, 'total_flos': 2.281669114761216e+16, 'train_loss': 0.8493731454242952, 'epoch': 35.39823008849557})

In [16]:
result = model.generate(test[2][0].unsqueeze(0).to("cuda"), max_length=20,
                                      min_length=20,
                                      length_penalty=2.0,
                                      num_beams=10, early_stopping=False)

In [17]:
tokenizer.decode(test[2][0], skip_special_tokens=True)

'Однажды зимним вечером тусили в хорошей дружеской компании и между делом затронули тему про «серые будни ИТ-шника». Про то, что многие концептуальные вещи (а не чисто ремесленные) плохо гуглятся и вызывают ступор у большинства начинающих процессных аналитиков и разработчиков. Ну и как-то так, слово за слово, пришли к идее о том, чтобы было бы здорово разбавить яркими красками и эмоциональными переживаниями сухой язык и весьма условные пиктограммы промышленных спецификаций. Так появился наш новый уникальный мерч, ну и прикольная динамичная настолка. Настолки весьма популярны среди команд разработки, такой формат многим заходит и оказывает благоприятное влияние на формирование коллективов. Но для их закрепления нужна какая-то понятная объединяющая идея. ИдеяМы решили попробовать простыми словами объяснить путь построения процессной компании, и при этом поиграться с описанными в спецификации BPMN 2.0 инструментами, посмотреть, какие они могут дать выгоды и как их можно эффективно комбини

In [18]:
tokenizer.decode(result[0], skip_special_tokens=True)

'процессов BPM Fab Доходность график gamedev свободный unreal Разработка'

In [19]:
loaded_model = T5ForConditionalGeneration.from_pretrained("test/checkpoint-4000", device_map="cpu")

In [22]:
%time

result = loaded_model.generate(test[2][0].unsqueeze(0), max_length=20,
                                      min_length=20,
                                      length_penalty=2.0,
                                      num_beams=10, early_stopping=False)

CPU times: user 18 µs, sys: 2 µs, total: 20 µs
Wall time: 477 µs


In [21]:
result

tensor([[    0,  6830,   850,   856,   934,   897,  4877,   422,   986,   370,
          5293,     8,  4252, 20543,  6568, 17276,  5888,  2045,   700, 23894]])